In [4]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

import os

from langchain.text_splitter import CharacterTextSplitter
from langchain_community.document_loaders import TextLoader
from langchain_community.vectorstores import Chroma
from langchain_openai import OpenAIEmbeddings, ChatOpenAI

from dotenv import load_dotenv

In [5]:
load_dotenv()

True

# Загрузка и чтение файлов в формате PDF

In [91]:
import os
import glob
import pdfplumber

# Указываем путь к директории
current_dir = os.getcwd()  # получаем текущую директорию
folder_path = os.path.join(current_dir, 'Intelion_books')

# Получаем список всех PDF файлов в директории
file_paths = glob.glob(os.path.join(folder_path, "*.pdf"))

# Проверка, есть ли файлы в директории
if not file_paths:
    print(f"В директории '{folder_path}' нет PDF файлов.")
else:
    print(f"Найдено {len(file_paths)} PDF файлов в директории '{folder_path}'.")

# Функция для чтения содержимого PDF файла с использованием pdfplumber
def read_pdf_with_plumber(file_path):
    with pdfplumber.open(file_path) as pdf:
        text = ""
        # Проходим по всем страницам PDF
        for page in pdf.pages:
            page_text = page.extract_text()
            if page_text:
                text += page_text
        return text

# Чтение всех PDF файлов
for file_path in file_paths:
    print(f"Чтение файла: {file_path}")
    pdf_content = read_pdf_with_plumber(file_path)
    
    # Проверка, пустое ли содержимое файла
    if not pdf_content.strip():  # Проверка на пустое содержимое
        print(f"Файл '{file_path}' пустой или не удалось извлечь текст.")
    else:
        print(f"Содержимое файла '{file_path}':")
        print(pdf_content)

Найдено 5 PDF файлов в директории '/Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books'.
Чтение файла: /Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/Анурьев, 1 том.pdf


Data-loss while decompressing corrupted data


Содержимое файла '/Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/Анурьев, 1 том.pdf':
УДК 621.001.66(035)
ББК 34.42я2
А73
Рецензенты:
доктор технических наук
A.Ф. Крайнев,
заслуженный деятель науки и техники РФ, доктор технических наук
B.М. Труханов
В справочнике использованы стандарты, действующие на 1 июня 2006 г.
Анурьев В.И.
А73 Справочник конструктора-машиностроителя: в 3-х т. Т. 1. - 9-е изд., перераб.
и доп./ под ред. И.Н. Жестковой. - М.: Машиностроение, 2006. - 928 с.
ISBN 5-217-03343-6 (Т. ])
ISBN 5-94275-273-7 (Т. 1)
В первом томе приведены общетехнические сведения, справочные данные по конструкци­
онным материалам, шероховатости поверхности, допускам и посадкам, предельным отклоне­
ниям формы и расположения поверхностей, конструктивным элементам деталей, крепежным
изделиям, стандартизованным и нормализованным деталям и узлам, защитно-декоративным
покрытиям металлов и пластмасс.
Девятое издание (8-е изд. 2000 г.) переработано в соответствии с но

In [92]:
# Объединение пути к текущему каталогу с подкаталогом "db" и именем каталога "chroma_db"
# Это создает полный путь к каталогу для хранения данных "chroma_db"
persistent_directory = os.path.join(current_dir, "db", "chroma_db_intelion_PDF")

db_dir = os.path.join(current_dir, "db")

# Чтение и разбиение файлов на чанки при помощи RecursiveCharacterTextSplitter

In [94]:
import os
import glob
import pdfplumber
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.schema import Document  # Импортируем класс Document

# Получаем текущий рабочий каталог
current_dir = os.getcwd()

# Указываем путь к директории с PDF файлами
folder_path = os.path.join(current_dir, 'Intelion_books')

# Получаем список всех PDF файлов в директории
file_paths = glob.glob(os.path.join(folder_path, "*.pdf"))

# Проверка, есть ли PDF файлы в директории
if not file_paths:
    raise FileNotFoundError(f"В директории {folder_path} не найдено PDF файлов.")

# Инициализация рекурсивного текстового сплиттера
text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=100)

# Чтение и обработка всех PDF файлов
docs = []
for file_path in file_paths:
    print(f"Чтение файла: {file_path}")
    
    try:
        # Открываем PDF файл с помощью pdfplumber
        with pdfplumber.open(file_path) as pdf:
            all_text = ""
            # Проходим по всем страницам и собираем текст
            for page_num, page in enumerate(pdf.pages):
                page_text = page.extract_text()
                if page_text:
                    all_text += page_text
            
            # Выводим количество страниц
            print(f"Файл {file_path} содержит {len(pdf.pages)} страниц.")

            # Разбиваем весь текст на части с использованием рекурсивного текстового сплиттера
            chunks = text_splitter.split_text(all_text)
            print(f"Файл {file_path} разбит на {len(chunks)} частей.")
            
            # Преобразуем текстовые части в объекты Document
            for chunk in chunks:
                doc = Document(page_content=chunk, metadata={"source": file_path})
                docs.append(doc)
            
    except Exception as e:
        print(f"Ошибка при чтении файла {file_path}: {e}")

Чтение файла: /Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/Анурьев, 1 том.pdf


Data-loss while decompressing corrupted data


Файл /Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/Анурьев, 1 том.pdf содержит 936 страниц.
Файл /Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/Анурьев, 1 том.pdf разбит на 3585 частей.
Чтение файла: /Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/chernavskii_sa_i_dr_proektirovanie_mekhanicheskikh_peredach.pdf
Файл /Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/chernavskii_sa_i_dr_proektirovanie_mekhanicheskikh_peredach.pdf содержит 559 страниц.
Файл /Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/chernavskii_sa_i_dr_proektirovanie_mekhanicheskikh_peredach.pdf разбит на 0 частей.
Чтение файла: /Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/Анурьев, 2 том.pdf
Файл /Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/Анурьев, 2 том.pdf содержит 968 страниц.
Файл /Users/sergey/Desktop/NN:N

# В качестве эмбеддингов используем text-embedding-3-small от OpenAI

In [6]:
# Загружаем модель эмбеддингов
embeddings = OpenAIEmbeddings(model="text-embedding-3-small",)

# Так как данных много их нужно разделить на батчи

In [101]:
# Функция для создания векторного хранилища с батчами
def create_vector_store_in_batches(docs, embeddings, batch_size, store_name, persistent_directory):
    # Инициализируем директорию для сохранения векторного хранилища
    if not os.path.exists(persistent_directory):
        os.makedirs(persistent_directory)

    # Выводим сообщение о начале создания векторного хранилища
    print(f"\n--- Создание векторного хранилища {store_name} ---")

    # Инициализируем хранилище Chroma
    db = Chroma(embedding_function=embeddings, persist_directory=persistent_directory)

    # Разбиваем документы на батчи и добавляем их в хранилище
    for i in range(0, len(docs), batch_size):
        batch_docs = docs[i:i + batch_size]
        print(f"Добавляем документы с {i} по {i + len(batch_docs) - 1}...")
        
        # Добавляем документы в хранилище по батчам
        db.add_documents(batch_docs)

    # Сохраняем изменения в векторном хранилище
    db.persist()

    # Сообщаем о завершении создания векторного хранилища
    print(f"--- Создание векторного хранилища завершено {store_name} ---")


batch_size = 1000  # Задаем размер батча
store_name = "Intelion_Vector_Store"



# Создание векторной базы данных

In [102]:
# Вызов функции создания векторного хранилища
create_vector_store_in_batches(docs, embeddings, batch_size, store_name, persistent_directory)



--- Создание векторного хранилища Intelion_Vector_Store ---
Добавляем документы с 0 по 999...
Добавляем документы с 1000 по 1999...
Добавляем документы с 2000 по 2999...
Добавляем документы с 3000 по 3999...
Добавляем документы с 4000 по 4999...
Добавляем документы с 5000 по 5999...
Добавляем документы с 6000 по 6999...
Добавляем документы с 7000 по 7999...
Добавляем документы с 8000 по 8999...
Добавляем документы с 9000 по 9999...
Добавляем документы с 10000 по 10999...
Добавляем документы с 11000 по 11466...
--- Создание векторного хранилища завершено Intelion_Vector_Store ---


# Загрузка векторной базы данных после ее создания или если она была создана ранее

In [7]:
import os
# from chromadb import Chroma  # Импортируем библиотеку Chroma

# Укажите путь к вашей базе данных
persistent_directory = "/Users/sergey/Desktop/RAG_Project/RAG_intelion/db/chroma_db_intelion_PDF"

# Проверьте, существует ли база данных
if os.path.exists(os.path.join(persistent_directory, "chroma.sqlite3")):
    print(f"Загружаем векторное хранилище из {persistent_directory}...")

    # Загружаем векторное хранилище
    db = Chroma(
        persist_directory=persistent_directory,  # Указываем путь к существующему хранилищу
        embedding_function=embeddings  # Передаем функцию эмбеддингов (нужна для поиска)
    )

Загружаем векторное хранилище из /Users/sergey/Desktop/RAG_Project/RAG_intelion/db/chroma_db_intelion_PDF...


/var/folders/h2/r9wh0x750xq4v5z33ylwrzw40000gn/T/ipykernel_9084/177577199.py:12: LangChainDeprecationWarning: The class `Chroma` was deprecated in LangChain 0.2.9 and will be removed in 1.0. An updated version of the class exists in the langchain-chroma package and should be used instead. To use it run `pip install -U langchain-chroma` and import as `from langchain_chroma import Chroma`.
  db = Chroma(


In [8]:
from langchain_core.messages import HumanMessage, SystemMessage

# Проверяем как работает поиск по базе данных

In [9]:
# Определяем вопрос, на который будем искать ответ
query = "Прутки оловянно фосфористой бронзы?"

# 1. Поиск по сходству без порога (search_type="similarity")
retriever_similarity = db.as_retriever(
    search_type="similarity",
    search_kwargs={"k": 3},
)

# Выполняем поиск
relevant_docs_similarity = retriever_similarity.invoke(query)

# Вывод результатов
print("\n--- Результаты поиска по сходству (без порога) ---")
for i, doc in enumerate(relevant_docs_similarity, 1):
    print(f"Документ {i}:\n{doc.page_content}\n")

# 2. Поиск с использованием функции search с порогом сходства
def search(query: str, db, k=3, similarity_threshold=0.4):
    # Поиск документов с оценками релевантности
    docs_scores = db.similarity_search_with_relevance_scores(query, k=k)
    # Фильтрация по порогу сходства
    good_documents = []
    for doc, score in docs_scores:
        if score > similarity_threshold:
            good_documents.append(doc.page_content)
    return good_documents

# Выполняем поиск с порогом
results_with_threshold = search(query, db=db, k=3, similarity_threshold=0.2)

# Вывод результатов
print("\n--- Результаты поиска с порогом сходства ---")
for i, content in enumerate(results_with_threshold, 3):
    print(f"Документ {i}:\n{content}\n")



--- Результаты поиска по сходству (без порога) ---
Документ 1:
Оловянно-фосфорнстые бронзы
Бр0ф2-0,25 —
— —
Бр0ф4-0,25 C5II00* CuSn4 (2.1016) C5110
C5I000
— — —
Бр0ф6,5-0,15 CuSn 6 (2.1020) C5191
—
С53200
— — —
БрОФб,5-0,4
— — —
Бр0ф7-0,2 С52100 CuSn8 (2.1030) C52I0
БрОФ8,0-0,3 CuSn8 (2.1030) C52I2
—
С52400
— — —
Оловянно-цинковые бронзы
БрОЦ4-3 — — —
— — CuSn6Zn6 (2.1080) —
Оловянно-цинко-свннцовые бронзы
БрОЦС4-4-0,25 — — —
— C54400 — —
Оловянно-никелевые бронзы
— C72500 CuNi9Sn2 (2.0875) —
— C72650 — —
— C72700 — —
— C72900 — —

Документ 2:
БрОЗЦ12С5 БрОЦСЗ-12-5 БрОбЦбСЗ
-
БрОЗЦ7С5Н1 БрОЦСНЗ-7-5-1 Бр08Ц4
—
Бр04Ц7С5 БрОЦСЗ,5-7-5 БрО 10Ф1
—
Бр04Ц4С17 БрОЦС4-4-17 БрОЮЦ2
—
Бр05Ц5С5 БрОЦС5-5-6 БрОЮСЮ
—
Бр05С25
—
69а. Марки аналогов литейных оловянных бронз по национальным стандартам
Россия, США, Германия, Япония,
ASTM D1N J1S
ГОСТ 613-79 В30; В427; В505; В584 17656 Н5111; Н5113; Н5115
Оловянно-фосфоритные бронзы
БрОЮФ1
— — —
С90700 Н5113/class2
— —
С90800 Н5113/class2B
—
С9П00
— —
С9130

# здесь добовляем генерацию ответа LLM

In [10]:
# Определяем вопрос, на который будем искать ответ
query = "Химический состав стали марок Fe360?"

# Получаем релевантные документы на основе запроса
retriever = db.as_retriever(
    search_type="similarity",  # Указываем тип поиска по сходству
    search_kwargs={"k": 5},  # Параметр: количество возвращаемых документов (k)
)

# Выполняем запрос к ретриверу для получения релевантных документов
relevant_docs = retriever.invoke(query)

# Выводим релевантные документы с их содержимым
print("\n--- Релевантные документы ---")
for i, doc in enumerate(relevant_docs, 1):
    # Выводим каждый документ с его содержимым и номером
    print(f"Документы {i}:\n{doc.page_content}\n")

# Объединяем запрос и содержимое релевантных документов в один текст для передачи модели
combined_input = (
    "Это некоторые документы которые могут помочь ответить на вопрос: "
    + query  # Включаем исходный запрос
    + "\n\nРелевантные документы:\n"  # Добавляем заголовок для раздела с документами
    + "\n\n".join([doc.page_content for doc in relevant_docs])  # Добавляем текст всех документов
    + "\n\nПожалуйста, предоставьте ответ, основываясь только на предоставленных документах. Если ответ не найден в документах, ответьте ‘Я не уверен'."  # Просим модель ответить только на основе предоставленных данных
)


# Создаем модель ChatOpenAI для обработки запроса
model = ChatOpenAI(model="gpt-4o-mini")

# Определяем сообщения, которые передаем модели
messages = [
    SystemMessage(content="Ты помошник который отвечает на вопросы пользователя."),  # Системное сообщение с инструкциями для модели
    HumanMessage(content=combined_input),  # Сообщение пользователя, содержащее запрос и документы
]

# Вызываем модель с подготовленными сообщениями
result = model.invoke(messages)

# Выводим сгенерированный ответ
print("\n--- Сгенерированный ответ ---")
# print("Full result:")  # Можно также вывести полный результат, если нужно
# print(result)
print("Текстовый ответ модели:")  # Выводим только текстовый ответ модели
print(result.content)


--- Релевантные документы ---
Документы 1:
Ст4кп Не более 0,05
Ст4пс 0,18...0,27 0,40...0,70 0,05...0,15
Ст4сп 0,15...0,30
Ст5пс 0,05...0,15
Ст5сп 0,28...0,37 0,50...0,80 0,15...0,30
Ст5Гпс 0,22... 0,30 0,80... 1,20 Не более 0,15
Стбпс 0,05...0,!5
0,38... 0,49 0,50...0,80
Стбсп 0,15...0,30V. Химический состав стали марок "Fe" по международным стандартам
ИСО 630-80 и ИСО 1052-82
Марка Категория Толщина Массовая доля элементов, %, не более Степень
стали качества проката, мм С Мп Si Р S N раскисления
Fe310 0 1,6 0,55
— — — — - —

Документы 2:
несколько затруднена из-за склонности к за­ ным стандартам ИСО 630--80 и ИСО 1052-82 в
калке околошовной зоны и образованию в ней части требований к химическому составу стали.
хрупких структур (требуется специальная тех­ Сопоставление марок стали типа "Ст" и
нология сварки).
типа "FeM по ИСО 630-80 и ИСО 1052-82 при­
3. Марганцовистые стали в состоянии про­
ведено в табл. 1.
ката или после нормализации имеют повы­
шенную прочность и упругость. Они о

In [11]:
from langchain.chains import create_history_aware_retriever, create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate, MessagesPlaceholder

# Вариант с выводом перефразированных вопросов

In [12]:
# Инициализируем retriever с типом поиска по схожести, чтобы получать k=3 наиболее релевантных результатов
retriever = db.as_retriever(
    search_type="similarity",  # Используем метод поиска по схожести
    search_kwargs={"k": 5},  # Количество возвращаемых результатов: 3
)

# Создаем модель ChatOpenAI с использованием модели GPT-4o
llm = ChatOpenAI(model="gpt-4o-mini")  # Модель GPT-4o для обработки запросов

# Определяем системный промпт для контекстуализации вопросов
# Этот промпт объясняет ИИ, как следует формулировать вопрос на основе истории чата
contextualize_q_system_prompt = (
    "Учитывая историю чата и последний вопрос пользователя, "  # Описание задачи
    "который может ссылаться на контекст из истории чата, "  # Учитывание истории чата
    "сформулируйте самодостаточный вопрос, который можно понять "  # Требование сделать вопрос самодостаточным
    "без использования истории чата. НЕ отвечайте на вопрос, просто "  # Не нужно отвечать, только переформулировать вопрос
    "переформулируйте его, если это необходимо, или верните его без изменений."
# )
    # "Вы являетесь ассистентом по языковой модели искусственного интеллекта."
    # "Ваша задача - сгенерировать 3 различных подвопросов Или альтернативных версий данного пользовательского вопроса для извлечения соответствующих документов из векторной базы данных."
    # "Сгенерировав несколько версий пользовательского вопроса, ваша цель - помочь пользователю преодолеть некоторые ограничения поиска сходства на основе расстояния."
    # "Создавая дополнительные вопросы, вы можете разбить вопросы, относящиеся к нескольким концепциям, на отдельные вопросы."
    # "Это поможет вам получить соответствующие документы для составления окончательного ответа"
    # "Если в вопросе присутствует несколько концепций, вам следует разбить его на подзадачи, задав по одному вопросу для каждой концепции"
    )

# Создаем шаблон для формирования контекстуализированных вопросов
contextualize_q_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", contextualize_q_system_prompt),  # Системное сообщение с инструкцией для ИИ
        MessagesPlaceholder("chat_history"),  # Место для истории чата
        ("human", "{input}"),  # Ввод пользователя, который нужно переформулировать
    ]
)

# Создаем retriever, учитывающий историю чата
# Этот retriever использует LLM для помощи в переформулировании вопросов с учетом контекста
history_aware_retriever = create_history_aware_retriever(
    llm, retriever, contextualize_q_prompt  # Используем созданный шаблон и retriever для поиска с историей
)

# Определяем системный промпт для ответа на вопросы
# Этот промпт объясняет ИИ, как отвечать на вопросы на основе контекста и что делать, если ответа нет
qa_system_prompt = (
    "Вы помощник для задач по ответам на вопросы о людях из русской Wikipedia. Используйте "  # Инструкция для ИИ
    "следующие части полученного контекста, чтобы ответить на "  # Использование контекста для ответа
    "вопрос. Если вы не знаете ответа, просто скажите, что вы "  # Если ответа нет, сообщить об этом
    "не знаете. Используйте максимум три предложения и дайте "  # Ответ должен быть кратким
    "краткий ответ."  # Старайтесь отвечать как можно более сжато
    "\n\n"
    "{context}"  # Контекст, который будет использован для ответа
)

# Создаем шаблон для формирования ответов на вопросы
qa_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", qa_system_prompt),  # Системное сообщение с инструкцией для ИИ
        MessagesPlaceholder("chat_history"),  # Место для истории чата
        ("human", "{input}"),  # Ввод пользователя, на который нужно ответить
    ]
)

# Создаем цепочку для объединения документов для ответов на вопросы
# `create_stuff_documents_chain` передает весь найденный контекст в LLM для обработки
question_answer_chain = create_stuff_documents_chain(llm, qa_prompt)

# Создаем retrieval-цепочку, которая объединяет retriever с историей и цепочку для ответов на вопросы
rag_chain = create_retrieval_chain(history_aware_retriever, question_answer_chain)


# # Функция для моделирования непрерывного чата
# def continual_chat():
#     print("Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.")  # Начало общения с ИИ
#     chat_history = []  # Хранение истории чата
#     while True:
#         query = input("ВЫ: ")  # Получение запроса от пользователя
#         if query.lower() == "выход":  # Если пользователь хочет завершить чат
#             break
#         # Обработка запроса пользователя через цепочку retrieval
#         result = rag_chain.invoke({"input": query, "chat_history": chat_history})  # Запрос к цепочке
#         # Печать вопроса пользователя и ответа ИИ
#         print(f"Вы: {query}")  # Печать вопроса пользователя
#         print(f"AI: {result['answer']}")  # Ответ ИИ
#         # Обновление истории чата
#         chat_history.append(HumanMessage(content=query))  # Добавление сообщения пользователя в историю
#         chat_history.append(SystemMessage(content=result["answer"]))  # Добавление ответа ИИ в историю

# # Main function to start the continual chat
# if __name__ == "__main__":
#     continual_chat()


# Функция для моделирования непрерывного чата с выводом переформулированного вопроса
def continual_chat():
    print("Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.")  # Начало общения с ИИ
    chat_history = []  # Хранение истории чата
    while True:
        query = input("ВЫ: ")  # Получение запроса от пользователя
        if query.lower() == "выход":  # Если пользователь хочет завершить чат
            break

        # Переформулировка вопроса через вызов LLM с контекстом
        reformulated_prompt = contextualize_q_prompt.format_messages(
            chat_history=chat_history, input=query
        )
        reformulated_query_result = llm(reformulated_prompt)  # Получаем объект AIMessage
        reformulated_query = reformulated_query_result.content  # Доступ к содержимому через атрибут content
        
        print(f"Переформулированный вопрос: {reformulated_query}")  # Вывод переформулированного вопроса
        
        # Обработка запроса пользователя через цепочку retrieval
        result = rag_chain.invoke({"input": reformulated_query, "chat_history": chat_history})  # Запрос к цепочке
        
        # Печать вопроса пользователя и ответа ИИ
        print(f"Вы: {query}")  # Печать вопроса пользователя
        print(f"AI: {result['answer']}")  # Ответ ИИ
        
        # Обновление истории чата
        chat_history.append(HumanMessage(content=query))  # Добавление сообщения пользователя в историю
        chat_history.append(SystemMessage(content=result["answer"]))  # Добавление ответа ИИ в историю

# Main function to start the continual chat
if __name__ == "__main__":
    continual_chat()

Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.


/var/folders/h2/r9wh0x750xq4v5z33ylwrzw40000gn/T/ipykernel_9084/2154766464.py:106: LangChainDeprecationWarning: The method `BaseChatModel.__call__` was deprecated in langchain-core 0.1.7 and will be removed in 1.0. Use invoke instead.
  reformulated_query_result = llm(reformulated_prompt)  # Получаем объект AIMessage


Переформулированный вопрос: Каков химический состав стали марки Fe360?
Вы: Химический состав стали марок Fe360?
AI: Сталь марки Fe360 относится к углеродистым сталям обыкновенного качества и имеет следующие характеристики: массовая доля углерода (C) не более 0,22%, марганца (Mn) до 1,6%, кремния (Si) до 0,55%, фосфора (P) и серы (S) не более 0,045%. Сталь также может быть классифицирована как спокойная (E) или мелкозернистая (CF) в зависимости от условий производства.
Переформулированный вопрос: Какие виды стали марки Fe360 существуют?
Вы: какие виды Сталь марки Fe360 ты знаешь?
AI: Существует несколько видов стали марки Fe360, включая Fe360-A, Fe360-B, Fe360-C и Fe360-D. Эти разновидности отличаются по химическому составу и механическим свойствам, что позволяет использовать их в различных условиях эксплуатации. Например, они могут иметь разные уровни прочности и вязкости.
Переформулированный вопрос: В чем заключаются основные различия между сталями марки Fe360-A и Fe360-B?
Вы: в чем о

Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.

Переформулированный вопрос: Каков химический состав стали марки Fe360?
Вы: Химический состав стали марок Fe360?
AI: Сталь марки Fe360 относится к углеродистым сталям обыкновенного качества и имеет следующие характеристики: массовая доля углерода (C) не более 0,22%, марганца (Mn) до 1,6%, кремния (Si) до 0,55%, фосфора (P) и серы (S) не более 0,045%. Сталь также может быть классифицирована как спокойная (E) или мелкозернистая (CF) в зависимости от условий производства.
Переформулированный вопрос: Какие виды стали марки Fe360 существуют?
Вы: какие виды Сталь марки Fe360 ты знаешь?
AI: Существует несколько видов стали марки Fe360, включая Fe360-A, Fe360-B, Fe360-C и Fe360-D. Эти разновидности отличаются по химическому составу и механическим свойствам, что позволяет использовать их в различных условиях эксплуатации. Например, они могут иметь разные уровни прочности и вязкости.
Переформулированный вопрос: В чем заключаются основные различия между сталями марки Fe360-A и Fe360-B?
Вы: в чем отличие между Fe360-A и Fe360-B?
AI: Основные различия между сталями марки Fe360-A и Fe360-B заключаются в содержании углерода и других легирующих элементов. Сталь Fe360-A имеет более низкое содержание углерода (не более 0,20%), в то время как в Fe360-B этот уровень может достигать 0,22%. Эти различия влияют на механические свойства, такие как прочность и вязкость.
Переформулированный вопрос: Какие еще марки стали существуют и каковы их основные характеристики?
Вы: какие еще виды стали ты знаешь?
AI: Существует множество марок стали, каждая из которых имеет свои характеристики. Например, сталь марки 08X13 (нержавеющая) обладает высокой коррозионной стойкостью и используется для деталей, подвергающихся агрессивным средам, а сталь марки 20X13 отличается повышенной пластичностью и используется в условиях ударных нагрузок. Другие марки, такие как 15Л К20 и 35Л К25, имеют свои пределы прочности и вязкости, что делает их подходящими для различных конструкций и деталей.
Переформулированный вопрос: Каковы основные размеры цилиндрических концов валов?
Вы:  Основные размеры  цилиндрических концов валов?
AI: Основные размеры цилиндрических концов валов зависят от диаметра вала и могут варьироваться. Например, для валов диаметром от 0,8 до 630 мм установлены различные размеры, а также предусмотрены резьбовые концы с определёнными параметрами. Эти размеры регулируются стандартами, такими как ГОСТ, и могут включать длину, диаметр и тип резьбы.
Переформулированный вопрос: Какие ГОСТы регулируют размеры цилиндрических концов валов?
Вы: А ГОСТы?
AI: Размеры цилиндрических концов валов регулируются несколькими ГОСТами, в том числе ГОСТ 25346-89 и ГОСТ 24071-97. Эти стандарты устанавливают размеры, предельные отклонения и другие параметры для цилиндрических валов и шпонок. Также могут применяться другие ГОСТы, связанные с конкретными условиями эксплуатации и типами валов.

In [13]:
from langchain_core.tools import Tool
from langchain import hub
from langchain.agents import AgentExecutor, create_structured_chat_agent, create_react_agent
from langchain.memory import ConversationBufferMemory
from langchain.chains import create_history_aware_retriever, create_retrieval_chain
from langchain_core.messages import AIMessage, HumanMessage

Respond to the human as helpfully and accurately as possible. You have access to the following tools:

{tools}

Use a json blob to specify a tool by providing an action key (tool name) and an action_input key (tool input).

Valid "action" values: "Final Answer" or {tool_names}

Provide only ONE action per $JSON_BLOB, as shown:

```
{{
  "action": $TOOL_NAME,
  "action_input": $INPUT
}}
```

Follow this format:

Question: input question to answer
Thought: consider previous and subsequent steps
Action:
```
$JSON_BLOB
```
Observation: action result
... (repeat Thought/Action/Observation N times)
Thought: I know what to respond
Action:
```
{{
  "action": "Final Answer",
  "action_input": "Final response to human"
}}

Begin! Reminder to ALWAYS respond with a valid json blob of a single action. Use tools if necessary. Respond directly if appropriate. Format is Action:```$JSON_BLOB```then Observation

# Здесь я использовал  ReAct Docstore для взаимодействия с пользователем (как он выглядит видно выше)

## Результат хороший но используется доп API

In [113]:
# Загружаем существующее хранилище векторов с функцией эмбеддинга
db = Chroma(persist_directory=persistent_directory,
            embedding_function=embeddings)  # Инициализируем хранилище векторов (Chroma) с указанием директории для хранения и функции эмбеддинга

# Создаем retriever для поиска по хранилищу векторов
# `search_type` указывает тип поиска (например, по схожести)
# `search_kwargs` содержит дополнительные параметры поиска (например, количество возвращаемых результатов)
retriever = db.as_retriever(
    search_type="similarity",  # Указываем тип поиска — по схожести
    search_kwargs={"k": 3},  # Возвращаем 3 наиболее релевантных результата
)

# Создаем модель ChatOpenAI
llm = ChatOpenAI(model="gpt-4o-mini", openai_api_key=os.getenv("OPENAI_API_KEY"))   # Используем модель GPT-4o для работы с текстовыми данными

# Определяем системный промпт для контекстуализации вопросов
# Этот промпт помогает ИИ понять, что необходимо переформулировать вопрос
# на основе истории чата, чтобы сделать его самодостаточным
contextualize_q_system_prompt = (
    "Учитывая историю чата и последний вопрос пользователя, "
    "который может ссылаться на контекст из истории чата, "
    "сформулируйте самодостаточный вопрос, который можно понять "
    "без использования истории чата. НЕ отвечайте на вопрос, просто "
    "переформулируйте его, если это необходимо, или верните его без изменений."
)

# Создаем шаблон для контекстуализации вопросов
contextualize_q_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", contextualize_q_system_prompt),  # Системное сообщение с инструкцией
        MessagesPlaceholder("chat_history"),  # Место для подстановки истории чата
        ("human", "{input}"),  # Ввод пользователя, который нужно переформулировать
    ]
)

# Создаем retriever, учитывающий историю чата
# Этот retriever использует LLM для переформулирования вопросов на основе истории чата
history_aware_retriever = create_history_aware_retriever(
    llm, retriever, contextualize_q_prompt  # Используем созданный шаблон и retriever для поиска с историей
)

# Определяем системный промпт для ответа на вопросы
# Этот промпт помогает ИИ давать краткие ответы, основываясь на полученном контексте
# и указывает, что делать, если ответа нет
qa_system_prompt = (
    "Вы помощник для задач по ответам на вопросы о людях из русской Wikipedia. Используйте "
    "следующие части полученного контекста, чтобы ответить на "
    "вопрос. Если вы не знаете ответа, просто скажите, что вы "
    "не знаете. Используйте максимум три предложения и дайте "
    "краткий ответ."
    "\n\n"
    "{context}"  # Подстановка контекста для ответа
)

# Создаем шаблон для формирования ответов на вопросы
qa_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", qa_system_prompt),  # Системное сообщение с инструкциями для ответа
        MessagesPlaceholder("chat_history"),  # История чата
        ("human", "{input}"),  # Ввод пользователя
    ]
)

# Создаем цепочку для объединения документов для ответов на вопросы
# `create_stuff_documents_chain` передает весь полученный контекст в LLM для обработки
question_answer_chain = create_stuff_documents_chain(llm, qa_prompt)

# Создаем retrieval-цепочку, которая объединяет retriever с историей и цепочку для ответов на вопросы
rag_chain = create_retrieval_chain(
    history_aware_retriever, question_answer_chain  # Комбинируем поиск и цепочку ответа на вопросы
)

# Настройка ReAct-агента с использованием хранилища документов для поиска
# Загружаем промпт ReAct Docstore для взаимодействия с пользователем через документы
react_docstore_prompt = hub.pull("hwchase17/react", api_key=os.getenv("LANGCHAIN_API_KEY"))  # Промпт для ReAct-агента

# Определяем инструменты, которые агент может использовать
tools = [
    Tool(
        name="Answer Question",  # Название инструмента
        func=lambda input, **kwargs: rag_chain.invoke(
            {"input": input, "chat_history": kwargs.get("chat_history", [])}
        ),  # Вызов функции для получения ответа с использованием цепочки поиска и истории
        description="Полезно для ответов на вопросы по контексту.",  # Описание инструмента
    )
]

# Создаем ReAct-агента с использованием хранилища документов
agent = create_react_agent(
    llm=llm,  # Языковая модель
    tools=tools,  # Инструменты, доступные агенту
    prompt=react_docstore_prompt,  # Промпт для взаимодействия
)

# Инициализируем AgentExecutor для управления взаимодействием между пользователем, агентом и инструментами
agent_executor = AgentExecutor.from_agent_and_tools(
    agent=agent, tools=tools, handle_parsing_errors=True, verbose=True,  # Обработка ошибок и вывод процесса
)

# Инициализируем историю чата
chat_history = []
while True:
    query = input("Вы: ")  # Получаем ввод пользователя
    if query.lower() == "exit":  # Если введен 'exit', завершаем цикл
        break
    response = agent_executor.invoke(
        {"input": query, "chat_history": chat_history})  # Агент обрабатывает запрос с учетом истории чата
    print(f"ИИ: {response['output']}")  # Выводим ответ агента

    # Обновляем историю чата
    chat_history.append(HumanMessage(content=query))  # Добавляем сообщение пользователя в историю
    chat_history.append(AIMessage(content=response["output"]))  # Добавляем ответ агента в историю

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/langsmith/client.py:5430: LangChainBetaWarning: The function `loads` is in beta. It is actively being worked on, so the API may change.
  prompt = loads(json.dumps(prompt_object.manifest))




> Entering new AgentExecutor chain...
Чтобы ответить на вопрос о химическом составе стали марки Fe360, мне нужно обратиться к информации о данном типе стали. 

Action: Answer Question  
Action Input: "Химический состав стали марки Fe360"  {'input': 'Химический состав стали марки Fe360', 'chat_history': [], 'context': [Document(metadata={'source': '/Users/sergey/Desktop/NN:NLP/NLP/NLPFinalProject/RAG_intelion/Intelion_books/Анурьев, 1 том.pdf'}, page_content='Ст4кп Не более 0,05\nСт4пс 0,18...0,27 0,40...0,70 0,05...0,15\nСт4сп 0,15...0,30\nСт5пс 0,05...0,15\nСт5сп 0,28...0,37 0,50...0,80 0,15...0,30\nСт5Гпс 0,22... 0,30 0,80... 1,20 Не более 0,15\nСтбпс 0,05...0,!5\n0,38... 0,49 0,50...0,80\nСтбсп 0,15...0,30V. Химический состав стали марок "Fe" по международным стандартам\nИСО 630-80 и ИСО 1052-82\nМарка Категория Толщина Массовая доля элементов, %, не более Степень\nстали качества проката, мм С Мп Si Р S N раскисления\nFe310 0 1,6 0,55\n— — — — - —'), Document(metadata={'source': '

In [114]:
from langchain.prompts import PromptTemplate
from langchain_core.output_parsers import JsonOutputParser, StrOutputParser

# Здесь я использовал проверу на галюцинации, оценки полезности и переписывания вопроса. 

## Работает как то странно..))

In [82]:
# # Инициализируем retriever с типом поиска по схожести, чтобы получать k=5 наиболее релевантных результатов
# retriever = db.as_retriever(
#     search_type="similarity",  # Используем метод поиска по схожести
#     search_kwargs={"k": 5},  # Количество возвращаемых результатов: 5
# )

# # Создаем модель ChatOpenAI с использованием модели GPT-4o
# llm = ChatOpenAI(model="gpt-4o-mini")  # Модель GPT-4o для обработки запросов

# # Определяем системный промпт для контекстуализации вопросов
# contextualize_q_system_prompt = (
#     "Учитывая историю чата и последний вопрос пользователя, "
#     "сформулируйте самодостаточный вопрос, который можно понять "
#     "без использования истории чата. НЕ отвечайте на вопрос, просто "
#     "переформулируйте его, если это необходимо, или верните его без изменений."
# )

# # Создаем шаблон для формирования контекстуализированных вопросов
# contextualize_q_prompt = ChatPromptTemplate.from_messages(
#     [
#         ("system", contextualize_q_system_prompt),
#         MessagesPlaceholder("chat_history"),
#         ("human", "{input}"),
#     ]
# )

# # Создаем retriever, учитывающий историю чата
# history_aware_retriever = create_history_aware_retriever(
#     llm, retriever, contextualize_q_prompt
# )

# # Определяем системный промпт для ответа на вопросы
# qa_system_prompt = (
#     "Вы помощник для задач по ответам на вопросы о людях из русской Wikipedia. "
#     "Используйте следующие части полученного контекста, чтобы ответить на вопрос. "
#     "Если вы не знаете ответа, просто скажите, что вы не знаете. "
#     "Используйте максимум три предложения и дайте краткий ответ.\n\n{context}"
# )

# # Создаем шаблон для формирования ответов на вопросы
# qa_prompt = ChatPromptTemplate.from_messages(
#     [
#         ("system", qa_system_prompt),
#         MessagesPlaceholder("chat_history"),
#         ("human", "{input}"),
#     ]
# )

# # Создаем цепочку для объединения документов для ответов на вопросы
# question_answer_chain = create_stuff_documents_chain(llm, qa_prompt)

# # Создаем retrieval-цепочку
# rag_chain = create_retrieval_chain(history_aware_retriever, question_answer_chain)

# # Шаблон для проверки галлюцинаций
# hallucination_prompt = PromptTemplate(
#     template="""Вы оценщик, проверяющий, основан ли ответ на фактах / поддерживается ли он фактическими данными. \n
#     Вот факты:
#     \n ------- \n
#     {documents} 
#     \n ------- \n
#     Вот ответ: {generation}
#     Дайте бинарную оценку в формате JSON с ключом 'score', где значение 'yes' или 'no', чтобы указать, поддерживается ли ответ фактами. \n
#     Пример: {{ "score": "yes" }}""",
#     input_variables=["generation", "documents"],
# )

# hallucination_grader = hallucination_prompt | llm | JsonOutputParser()

# def check_hallucination(generation, documents):
#     result = hallucination_grader.invoke({"generation": generation, "documents": documents})
#     print(f"Результат проверки на галлюцинации: {result}")
#     return result["score"]

# # Шаблон для оценки полезности
# usefulness_prompt = PromptTemplate(
#     template="""Вы оценщик, проверяющий, полезен ли ответ для решения вопроса. \n 
#     Вот ответ:
#     \n ------- \n
#     {generation} 
#     \n ------- \n
#     Вот вопрос: {question}
#     Дайте бинарную оценку в формате JSON с ключом 'score', где значение 'yes' или 'no'. \n
#     Пример: {{ "score": "yes" }}""",
#     input_variables=["generation", "question"],
# )

# answer_grader = usefulness_prompt | llm | JsonOutputParser()

# def check_usefulness(generation, question):
#     result = answer_grader.invoke({"generation": generation, "question": question})
#     print(f"Результат проверки на полезность: {result}")
#     return result["score"]

# # Шаблон для переписывания вопроса
# re_write_prompt = PromptTemplate(
#     template="""Вы переписыватель вопросов. Преобразуйте исходный вопрос в версию, оптимизированную для поиска в векторном хранилище. \n
#     Исходный вопрос: {question}. \n 
#     Улучшенный вопрос без предисловия: """,
#     input_variables=["question"],
# )

# question_rewriter = re_write_prompt | llm | StrOutputParser()

# def rewrite_question(question):
#     result = question_rewriter.invoke({"question": question})
#     print(f"Оптимизированный вопрос для поиска: {result}")
#     return result

# # Функция для моделирования непрерывного чата с проверкой галлюцинаций и полезности ответа
# def continual_chat():
#     print("Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.")  # Начало общения с ИИ
#     chat_history = []  # Хранение истории чата
#     while True:
#         query = input("ВЫ: ")  # Получение запроса от пользователя
#         if query.lower() == "выход":  # Если пользователь хочет завершить чат
#             break

#         # Выводим системный промпт для контекстуализации вопроса
#         print("\nСистемный промпт для контекстуализации вопроса:")
#         print(contextualize_q_system_prompt)

#         # Переписывание вопроса для оптимизации
#         improved_query = rewrite_question(query)
#         print(f"Переписанный вопрос: {improved_query}")

#         # Проверяем корректность перед отправкой
#         print(f"Отправляемый запрос: {improved_query}")
#         print(f"История чата: {chat_history}")

#         # Обработка запроса пользователя через цепочку retrieval
#         result = rag_chain.invoke({"input": improved_query, "chat_history": chat_history})

#         # Получаем сгенерированный ответ
#         generation = result['answer']

#         # Выводим системный промпт для ответа на вопрос
#         print("\nСистемный промпт для ответа на вопрос:")
#         print(qa_system_prompt)

#         # Проверка на галлюцинации
#         docs = retriever.get_relevant_documents(improved_query)
#         hallucination_score = check_hallucination(generation, docs)
#         print(f"Проверка на галлюцинации: {hallucination_score}")

#         # Проверка на полезность
#         usefulness_score = check_usefulness(generation, improved_query)
#         print(f"Проверка на полезность: {usefulness_score}")
        
#         # Печать вопроса пользователя и ответа ИИ
#         print(f"Вы: {query}")  # Печать вопроса пользователя
#         print(f"AI: {generation}")  # Ответ ИИ
        
#         # Обновление истории чата
#         chat_history.append(HumanMessage(content=query))  # Добавление сообщения пользователя в историю
#         chat_history.append(SystemMessage(content=generation))  # Добавление ответа ИИ в историю

# # Main function to start the continual chat
# if __name__ == "__main__":
#     continual_chat()

Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.

Системный промпт для контекстуализации вопроса:
Учитывая историю чата и последний вопрос пользователя, сформулируйте самодостаточный вопрос, который можно понять без использования истории чата. НЕ отвечайте на вопрос, просто переформулируйте его, если это необходимо, или верните его без изменений.
Оптимизированный вопрос для поиска: Кто такой Александр Овечкин?
Переписанный вопрос: Кто такой Александр Овечкин?
Отправляемый запрос: Кто такой Александр Овечкин?
История чата: []

Системный промпт для ответа на вопрос:
Вы помощник для задач по ответам на вопросы о людях из русской Wikipedia. Используйте следующие части полученного контекста, чтобы ответить на вопрос. Если вы не знаете ответа, просто скажите, что вы не знаете. Используйте максимум три предложения и дайте краткий ответ.

{context}
Результат проверки на галлюцинации: {'score': 'yes'}
Проверка на галлюцинации: yes
Результат проверки на полезность: {'score': 'yes

# Самый рабочий вариант 

In [115]:
# Инициализируем retriever с типом поиска по схожести, чтобы получать k=3 наиболее релевантных результатов
retriever = db.as_retriever(
    search_type="similarity",  # Используем метод поиска по схожести
    search_kwargs={"k": 5},  # Количество возвращаемых результатов: 3
)

# Создаем модель ChatOpenAI с использованием модели GPT-4o
llm = ChatOpenAI(model="gpt-4o-mini", temperature=0)  # Модель GPT-4o для обработки запросов

# Определяем системный промпт для контекстуализации вопросов
# Этот промпт объясняет ИИ, как следует формулировать вопрос на основе истории чата
contextualize_q_system_prompt = (
    "Учитывая историю чата и последний вопрос пользователя, "  # Описание задачи
    "который может ссылаться на контекст из истории чата, "  # Учитывание истории чата
    "сформулируйте самодостаточный вопрос, который можно понять "  # Требование сделать вопрос самодостаточным
    "без использования истории чата. НЕ отвечайте на вопрос, просто "  # Не нужно отвечать, только переформулировать вопрос
    "переформулируйте его, если это необходимо, или верните его без изменений."
# )
    # "Вы являетесь ассистентом по языковой модели искусственного интеллекта."
    # "Ваша задача - сгенерировать 3 различных подвопросов Или альтернативных версий данного пользовательского вопроса для извлечения соответствующих документов из векторной базы данных."
    # "Сгенерировав несколько версий пользовательского вопроса, ваша цель - помочь пользователю преодолеть некоторые ограничения поиска сходства на основе расстояния."
    # "Создавая дополнительные вопросы, вы можете разбить вопросы, относящиеся к нескольким концепциям, на отдельные вопросы."
    # "Это поможет вам получить соответствующие документы для составления окончательного ответа"
    # "Если в вопросе присутствует несколько концепций, вам следует разбить его на подзадачи, задав по одному вопросу для каждой концепции"
    )

# Создаем шаблон для формирования контекстуализированных вопросов
contextualize_q_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", contextualize_q_system_prompt),  # Системное сообщение с инструкцией для ИИ
        MessagesPlaceholder("chat_history"),  # Место для истории чата
        ("human", "{input}"),  # Ввод пользователя, который нужно переформулировать
    ]
)

# Создаем retriever, учитывающий историю чата
# Этот retriever использует LLM для помощи в переформулировании вопросов с учетом контекста
history_aware_retriever = create_history_aware_retriever(
    llm, retriever, contextualize_q_prompt  # Используем созданный шаблон и retriever для поиска с историей
)

# Определяем системный промпт для ответа на вопросы
# Этот промпт объясняет ИИ, как отвечать на вопросы на основе контекста и что делать, если ответа нет
qa_system_prompt = (
    "Вы помощник для задач по ответам на вопросы о людях из русской Wikipedia. Используйте "  # Инструкция для ИИ
    "следующие части полученного контекста, чтобы ответить на "  # Использование контекста для ответа
    "вопрос. Если вы не знаете ответа, просто скажите, что вы "  # Если ответа нет, сообщить об этом
    "не знаете. Используйте максимум три предложения и дайте "  # Ответ должен быть кратким
    "краткий ответ."  # Старайтесь отвечать как можно более сжато
    "\n\n"
    "{context}"  # Контекст, который будет использован для ответа
)

# Создаем шаблон для формирования ответов на вопросы
qa_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", qa_system_prompt),  # Системное сообщение с инструкцией для ИИ
        MessagesPlaceholder("chat_history"),  # Место для истории чата
        ("human", "{input}"),  # Ввод пользователя, на который нужно ответить
    ]
)

# Создаем цепочку для объединения документов для ответов на вопросы
# `create_stuff_documents_chain` передает весь найденный контекст в LLM для обработки
question_answer_chain = create_stuff_documents_chain(llm, qa_prompt)

# Создаем retrieval-цепочку, которая объединяет retriever с историей и цепочку для ответов на вопросы
rag_chain = create_retrieval_chain(history_aware_retriever, question_answer_chain)


# Функция для моделирования непрерывного чата
def continual_chat():
    print("Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.")  # Начало общения с ИИ
    chat_history = []  # Хранение истории чата
    while True:
        query = input("ВЫ: ")  # Получение запроса от пользователя
        if query.lower() == "выход":  # Если пользователь хочет завершить чат
            break
        # Обработка запроса пользователя через цепочку retrieval
        result = rag_chain.invoke({"input": query, "chat_history": chat_history})  # Запрос к цепочке
        # Печать вопроса пользователя и ответа ИИ
        print(f"Вы: {query}")  # Печать вопроса пользователя
        print(f"AI: {result['answer']}")  # Ответ ИИ
        # Обновление истории чата
        chat_history.append(HumanMessage(content=query))  # Добавление сообщения пользователя в историю
        chat_history.append(SystemMessage(content=result["answer"]))  # Добавление ответа ИИ в историю

# Main function to start the continual chat
if __name__ == "__main__":
    continual_chat()


# # # Функция для моделирования непрерывного чата с выводом переформулированного вопроса
# # def continual_chat():
# #     print("Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.")  # Начало общения с ИИ
# #     chat_history = []  # Хранение истории чата
# #     while True:
# #         query = input("ВЫ: ")  # Получение запроса от пользователя
# #         if query.lower() == "выход":  # Если пользователь хочет завершить чат
# #             break

# #         # Переформулировка вопроса через вызов LLM с контекстом
# #         reformulated_prompt = contextualize_q_prompt.format_messages(
# #             chat_history=chat_history, input=query
# #         )
# #         reformulated_query_result = llm(reformulated_prompt)  # Получаем объект AIMessage
# #         reformulated_query = reformulated_query_result.content  # Доступ к содержимому через атрибут content
        
# #         print(f"Переформулированный вопрос: {reformulated_query}")  # Вывод переформулированного вопроса
        
# #         # Обработка запроса пользователя через цепочку retrieval
# #         result = rag_chain.invoke({"input": reformulated_query, "chat_history": chat_history})  # Запрос к цепочке
        
# #         # Печать вопроса пользователя и ответа ИИ
# #         print(f"Вы: {query}")  # Печать вопроса пользователя
# #         print(f"AI: {result['answer']}")  # Ответ ИИ
        
# #         # Обновление истории чата
# #         chat_history.append(HumanMessage(content=query))  # Добавление сообщения пользователя в историю
# #         chat_history.append(SystemMessage(content=result["answer"]))  # Добавление ответа ИИ в историю

# # # Main function to start the continual chat
# # if __name__ == "__main__":
# #     continual_chat()

Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.
Вы: химический состав стали Fe360
AI: Химический состав стали Fe360 включает следующие элементы: углерод (C) до 0,20%, марганец (Mn) 1,6%, кремний (Si) 0,55%, фосфор (P) не более 0,050%, сера (S) не более 0,050%. Сталь также может содержать азот (N) не более 0,009%.
Вы: а Fe360 С
AI: Химический состав стали Fe360-C включает углерод (C) до 0,22%, марганец (Mn) 1,6%, кремний (Si) 0,55%, фосфор (P) не более 0,045% и серу (S) не более 0,045%.
Вы: расскажи про рекомендуемые посадки сопрягаемых деталей
AI: Рекомендуемые посадки сопрягаемых деталей включают в себя различные типы соединений, такие как шпоночные, шлицевые и резьбовые. При выборе посадок следует учитывать характер сопряжения (подвижное или неподвижное) и отдавать предпочтение рекомендуемым посадкам, установленным стандартами, например, ГОСТ 25347—82. Важно также учитывать допуски и предельные отклонения для обеспечения правильной сборки и функционирования деталей.


# Поиск документов с использованием RAG-Fusion и RRF для поиска и ранжирования документов:
## После переформулировки вопрос передается в генерацию нескольких запросов, и система выполняет поиск документов для каждого из них.

# Этот вариант работает медленнее и не сказал бы что ответы лучше

In [14]:
from langchain.prompts import ChatPromptTemplate
from langchain_openai import ChatOpenAI
from langchain_core.output_parsers import StrOutputParser
from langchain.load import dumps, loads
from operator import itemgetter
from langchain_core.runnables import RunnablePassthrough

# Инициализируем retriever с типом поиска по схожести, чтобы получать k=5 наиболее релевантных результатов
retriever = db.as_retriever(
    search_type="similarity",  # Используем метод поиска по схожести
    search_kwargs={"k": 5},  # Количество возвращаемых результатов
)

# Создаем модель ChatOpenAI с использованием модели GPT-4o
llm = ChatOpenAI(model="gpt-4o-mini")  # Модель GPT-4o для обработки запросов

# Определяем системный промпт для контекстуализации вопросов
contextualize_q_system_prompt = (
    "Учитывая историю чата и последний вопрос пользователя, "
    "который может ссылаться на контекст из истории чата, "
    "сформулируйте самодостаточный вопрос, который можно понять "
    "без использования истории чата. НЕ отвечайте на вопрос, просто "
    "переформулируйте его, если это необходимо, или верните его без изменений."
)

# Создаем шаблон для формирования контекстуализированных вопросов
contextualize_q_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", contextualize_q_system_prompt),  # Системное сообщение с инструкцией для ИИ
        MessagesPlaceholder("chat_history"),  # Место для истории чата
        ("human", "{input}"),  # Ввод пользователя, который нужно переформулировать
    ]
)

# Шаблон для генерации нескольких запросов
template = """Вы являетесь полезным помощником, который генерирует несколько поисковых запросов на основе одного входного запроса. \n
Сгенерируйте несколько поисковых запросов, связанных с: {question} \n
Output (4 queries):"""

prompt_rag_fusion = ChatPromptTemplate.from_template(template)

# Функция для генерации нескольких запросов
generate_queries = (
    prompt_rag_fusion 
    | ChatOpenAI(temperature=0) 
    | StrOutputParser() 
    | (lambda x: x.split("\n"))
)

# Функция для Reciprocal Rank Fusion
def reciprocal_rank_fusion(results: list[list], k=60):
    """Функция RRF для слияния результатов поиска из нескольких списков."""
    fused_scores = {}
    for docs in results:
        for rank, doc in enumerate(docs):
            doc_str = dumps(doc)
            if doc_str not in fused_scores:
                fused_scores[doc_str] = 0
            fused_scores[doc_str] += 1 / (rank + k)
    
    reranked_results = [
        (loads(doc), score)
        for doc, score in sorted(fused_scores.items(), key=lambda x: x[1], reverse=True)
    ]
    
    return reranked_results

# Функция для создания retrieval-цепочки с использованием RAG и RRF
def create_rag_fusion_retrieval_chain(retriever, question):
    # Генерируем несколько запросов
    generated_queries = generate_queries.invoke({"question": question})
    
    # Выполняем поиск по базе данных для каждого запроса
    search_results = [retriever.get_relevant_documents(query) for query in generated_queries]
    
    # Применяем RRF для слияния результатов
    reranked_docs = reciprocal_rank_fusion(search_results)
    
    # Извлекаем только документы, без их рангов
    return [doc for doc, score in reranked_docs]

# Создаем шаблон для ответа на вопросы на основе контекста
qa_system_prompt = (
    "Вы помощник для задач по ответам на вопросы о людях из русской Wikipedia. Используйте "
    "следующие части полученного контекста, чтобы ответить на "
    "вопрос. Если вы не знаете ответа, просто скажите, что вы "
    "не знаете. Используйте максимум три предложения и дайте "
    "краткий ответ.\n\n"
    "{context}"
)

qa_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", qa_system_prompt),
        MessagesPlaceholder("chat_history"),
        ("human", "{input}"),
    ]
)

# Функция для обработки запроса с контекстуализацией и RAG
def process_query(query, chat_history):
    # Шаг 1: Переформулируем вопрос с учетом истории чата
    reformulated_prompt = contextualize_q_prompt.format_messages(
        chat_history=chat_history, input=query
    )
    reformulated_query_result = llm(reformulated_prompt)  # Получаем объект AIMessage
    reformulated_query = reformulated_query_result.content  # Доступ к содержимому
    
    # Шаг 2: Получаем документы с использованием RAG-Fusion и RRF
    docs = create_rag_fusion_retrieval_chain(retriever, reformulated_query)
    
    # Шаг 3: Генерируем ответ на основе контекста
    result = question_answer_chain.invoke({"input": query, "context": docs, "chat_history": chat_history})
    
    return result

# Функция для моделирования непрерывного чата
def continual_chat():
    print("Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.")
    chat_history = []  # Хранение истории чата
    while True:
        query = input("ВЫ: ")  # Получение запроса от пользователя
        if query.lower() == "выход":  # Если пользователь хочет завершить чат
            break
        
        # Обрабатываем запрос пользователя через систему RAG с RRF
        result = process_query(query, chat_history)
        
        # Печать вопроса пользователя и ответа ИИ
        print(f"Вы: {query}")
        print(f"AI: {result}")  # Выводим результат, так как это строка
        
        # Обновление истории чата
        chat_history.append(HumanMessage(content=query))
        chat_history.append(SystemMessage(content=result))

# Запуск непрерывного чата
if __name__ == "__main__":
    continual_chat()

Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.


/var/folders/h2/r9wh0x750xq4v5z33ylwrzw40000gn/T/ipykernel_9084/2347212760.py:74: LangChainDeprecationWarning: The method `BaseRetriever.get_relevant_documents` was deprecated in langchain-core 0.1.46 and will be removed in 1.0. Use invoke instead.
  search_results = [retriever.get_relevant_documents(query) for query in generated_queries]
/var/folders/h2/r9wh0x750xq4v5z33ylwrzw40000gn/T/ipykernel_9084/2347212760.py:62: LangChainBetaWarning: The function `loads` is in beta. It is actively being worked on, so the API may change.
  (loads(doc), score)


Вы: Химический состав стали марок Fe360?
AI: Химический состав стали марки Fe360 включает следующие элементы: углерод (C) - не более 0,20%, марганец (Mn) - не более 1,6%, кремний (Si) - не более 0,55%. Также содержание фосфора (P) и серы (S) не должно превышать 0,045%.
Вы: какие виды Сталь марки Fe360 ты знаешь?
AI: Существуют несколько видов стали марки Fe360, включая Fe360-A, Fe360-B, Fe360-C и Fe360-D. Эти виды различаются по химическому составу и механическим свойствам.
Вы: в чем отличие между Fe360-A и Fe360-B?
AI: Основное отличие между Fe360-A и Fe360-B заключается в содержании углерода и других легирующих элементов, что влияет на их механические свойства. Конкретные значения для содержания углерода и других элементов могут различаться, что определяет их применение в различных условиях.
Вы: какие еще виды стали ты знаешь?
AI: Я знаю множество видов стали, включая углеродистые стали, легированные стали, нержавеющие стали, инструментальные стали и специальные стали, такие как высо

Начните общение с ИИ! Введите ‘выход’, чтобы завершить разговор.

Вы: Химический состав стали марок Fe360?
AI: Химический состав стали марки Fe360 включает следующие элементы: углерод (C) - не более 0,20%, марганец (Mn) - не более 1,6%, кремний (Si) - не более 0,55%. Также содержание фосфора (P) и серы (S) не должно превышать 0,045%.
Вы: какие виды Сталь марки Fe360 ты знаешь?
AI: Существуют несколько видов стали марки Fe360, включая Fe360-A, Fe360-B, Fe360-C и Fe360-D. Эти виды различаются по химическому составу и механическим свойствам.
Вы: в чем отличие между Fe360-A и Fe360-B?
AI: Основное отличие между Fe360-A и Fe360-B заключается в содержании углерода и других легирующих элементов, что влияет на их механические свойства. Конкретные значения для содержания углерода и других элементов могут различаться, что определяет их применение в различных условиях.
Вы: какие еще виды стали ты знаешь?
AI: Я знаю множество видов стали, включая углеродистые стали, легированные стали, нержавеющие стали, инструментальные стали и специальные стали, такие как высокопрочные и жаростойкие стали. Также есть стали, классифицированные по различным стандартам, например, марки по ГОСТ, ASTM, ISO и другим. Каждая категория стали имеет свои характеристики и области применения.
Вы:  Основные размеры  цилиндрических концов валов?
AI: Основные размеры цилиндрических концов валов включают диаметр, длину цилиндрической и резьбовой частей, а также параметры резьбы. Эти размеры зависят от диаметра вала и устанавливаются в соответствии с ГОСТ, при этом размеры могут варьироваться в зависимости от назначения и конструкции валов. Рекомендуемые размеры также могут быть согласованы между потребителем и разработчиком машин.
Вы: А ГОСТы?
AI: Основные ГОСТы, регулирующие размеры цилиндрических концов валов, включают ГОСТ 12080-66 и ГОСТ 12081-72. Эти стандарты определяют размеры, допуски и требования к конструкции валов с резьбовыми концами. Также существуют ГОСТы для шпонок и других элементов, связанных с валами, например, ГОСТ 24071-97 и ГОСТ 23360-78.